In [1]:
import datetime as dt
import pandas as pd
import warnings
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
pd.set_option('display.float_format', lambda x: '%.5f' % x)
warnings.simplefilter(action='ignore', category=Warning)

### Görev 1 Veriyi Anlama ve Hazırlama

In [2]:
df_ = pd.read_excel("online_retail_II-230817-120704.xlsx", sheet_name="Year 2010-2011")
df = df_.copy()

In [3]:
df.head()

Invoice StockCode                          Description  Quantity  \
0  536365    85123A   WHITE HANGING HEART T-LIGHT HOLDER         6   
1  536365     71053                  WHITE METAL LANTERN         6   
2  536365    84406B       CREAM CUPID HEARTS COAT HANGER         8   
3  536365    84029G  KNITTED UNION FLAG HOT WATER BOTTLE         6   
4  536365    84029E       RED WOOLLY HOTTIE WHITE HEART.         6   

          InvoiceDate   Price  Customer ID         Country  
0 2010-12-01 08:26:00 2.55000  17850.00000  United Kingdom  
1 2010-12-01 08:26:00 3.39000  17850.00000  United Kingdom  
2 2010-12-01 08:26:00 2.75000  17850.00000  United Kingdom  
3 2010-12-01 08:26:00 3.39000  17850.00000  United Kingdom  
4 2010-12-01 08:26:00 3.39000  17850.00000  United Kingdom

In [4]:
df.shape

(541910, 8)

In [5]:
df.describe().T

count                           mean                  min  \
Quantity    541910.00000                        9.55223         -80995.00000   
InvoiceDate       541910  2011-07-04 13:35:22.342307584  2010-12-01 08:26:00   
Price       541910.00000                        4.61114         -11062.06000   
Customer ID 406830.00000                    15287.68416          12346.00000   

                             25%                  50%                  75%  \
Quantity                 1.00000              3.00000             10.00000   
InvoiceDate  2011-03-28 11:34:00  2011-07-19 17:17:00  2011-10-19 11:27:00   
Price                    1.25000              2.08000              4.13000   
Customer ID          13953.00000          15152.00000          16791.00000   

                             max        std  
Quantity             80995.00000  218.08096  
InvoiceDate  2011-12-09 12:50:00        NaN  
Price                38970.00000   96.75977  
Customer ID          18287.00000 1713.60307

In [6]:
df.isnull().sum()

Invoice             0
StockCode           0
Description      1454
Quantity            0
InvoiceDate         0
Price               0
Customer ID    135080
Country             0
dtype: int64

In [7]:
df.dropna(inplace=True)
df.shape

(406830, 8)

In [8]:
# Eşsiz ürün sayısı kaç
df["StockCode"].nunique()

3684

In [9]:
# Hangi üründen kaçar tane var
df["StockCode"].value_counts()

StockCode
85123A          2077
22423           1905
85099B          1662
84879           1418
47566           1416
20725           1359
22720           1232
POST            1197
20727           1126
22197           1118
23203           1115
22383           1103
21212           1080
23209           1040
23298           1036
22086           1029
22382           1021
20728           1012
22457            997
22469            996
22384            977
22960            974
21034            955
22727            932
23206            907
82482            905
22386            903
22993            902
22138            894
22666            890
22961            888
20726            861
23084            857
22699            854
22139            849
22178            849
82494L           836
22470            835
22726            831
20914            818
22411            814
21931            800
23202            788
23301            779
23201            775
20724            767
23245            764
226

In [10]:
df.groupby("StockCode").agg({"Quantity":"sum"}).sort_values(by="Quantity",ascending=False).head(5)

Quantity
StockCode          
84077         53215
22197         48712
85099B        45066
84879         35314
85123A        34204

In [11]:
# Faturalardaki ‘C’ iptal edilen işlemleri göstermektedir. İptal edilen işlemleri veri setinden çıkarmamız lazım
df = df[~df["Invoice"].str.contains("C", na=False)]

In [12]:
df["TotalPrice"] = df["Quantity"] * df["Price"]

## Görev 2 RFM Metriklerinin Hesaplanması
* Recency, Frequency ve Monetary tanımlarını yapınız.
* Müşteri özelinde Recency, Frequency ve Monetary metriklerini groupby, agg ve lambda ile hesaplayınız.
* Hesapladığınız metrikleri rfmisimli bir değişkene atayınız.
* Oluşturduğunuz metriklerin isimlerini recency, frequency ve monetary olarak değiştiriniz.

* Not 1: recency değeri için bugünün tarihini (2011, 12, 11) olarak kabul ediniz.
* Not 2: rfm dataframe’ini oluşturduktan sonra veri setini "monetary>0" olacak şekilde filtreleyiniz.

In [13]:
df["InvoiceDate"].max()

Timestamp('2011-12-09 12:50:00')

In [14]:
today_date = dt.datetime(2011, 12, 11)
rfm = df.groupby('Customer ID').agg({'InvoiceDate': lambda date: (today_date - date.max()).days,'Invoice': lambda num: num.nunique(),'TotalPrice': lambda TotalPrice: TotalPrice.sum()})
rfm

InvoiceDate  Invoice   TotalPrice
Customer ID                                   
12346.00000          326        1  77183.60000
12347.00000            3        7   4310.00000
12348.00000           76        4   1797.24000
12349.00000           19        1   1757.55000
12350.00000          311        1    334.40000
12352.00000           37        8   2506.04000
12353.00000          205        1     89.00000
12354.00000          233        1   1079.40000
12355.00000          215        1    459.40000
12356.00000           23        3   2811.43000
12357.00000           34        1   6207.67000
12358.00000            2        2   1168.06000
12359.00000           58        4   6372.58000
12360.00000           53        3   2662.06000
12361.00000          288        1    189.90000
12362.00000            4       10   5226.23000
12363.00000          110        2    552.00000
12364.00000            8        4   1313.10000
12365.00000          292        2    641.38000
12367.00000            5        1    168.90000
12370.00000           52        4   3545.69000
12371.00000           45        2   1887.96000
12372.00000           72        3   1298.04000
12373.00000          312        1    364.60000
12374.00000           26        1    742.93000
12375.00000           11        2    457.50000
12377.00000          316        2   1628.12000
12378.00000          130        1   4008.62000
12379.00000           82        2    852.24000
12380.00000           22        4   2724.81000
12381.00000            5        5   1845.31000
12383.00000          185        5   1850.56000
12384.00000           29        2    585.27000
12386.00000          338        2    401.90000
12388.00000           16        6   2780.66000
12390.00000           80        1    549.84000
12391.00000           22        1    460.89000
12393.00000           73        4   1582.60000
12394.00000           64        2   1272.48000
12395.00000           20       12   3018.63000
12397.00000           36        2   2409.90000
12398.00000           46        1   1635.66000
12399.00000          120        4   1108.65000
12401.00000          304        1     84.30000
12402.00000          324        1    225.60000
12403.00000           50        1    427.70000
12405.00000          149        1   1710.39000
12406.00000           23        2   3415.30000
12407.00000           50        5   1708.12000
12408.00000           33        5   2888.55000
12409.00000           79        3  11072.67000
12410.00000          309        2    693.33000
12412.00000           75        3   1226.88000
12413.00000           67        3    758.10000
12414.00000          218        3    562.41000
12415.00000           25       21 124914.53000
12417.00000            4        9   3649.10000
12418.00000          113        1    668.58000
12420.00000           64        1    600.39000
12421.00000           16        4    807.04000
12422.00000           96        3    803.56000
12423.00000            1        8   1859.31000
12424.00000          163        2   1760.96000
12425.00000           79        1    777.20000
12426.00000          195        1    582.73000
12427.00000           22        3    825.80000
12428.00000           26        9   7956.46000
12429.00000           10        4   3750.40000
12430.00000           44        1    256.40000
12431.00000           36       15   6487.45000
12432.00000           43        5   5059.32000
12433.00000            1        7  13375.87000
12434.00000           85        2    806.14000
12435.00000           80        2   7829.89000
12436.00000          100        1    509.01000
12437.00000            2       18   4951.41000
12438.00000           15        2   2906.85000
12441.00000          367        1    173.55000
12442.00000            4        1    172.06000
12444.00000           22        5   5005.46000
12445.00000           23        1    133.40000
12446.00000           58        1   1002.31000
12447.00000          244        1    476.49000
12448.00000       

In [15]:
rfm.columns = ['recency', 'frequency', 'monetary']
rfm = rfm[rfm["monetary"] > 0]
rfm

recency  frequency     monetary
Customer ID                                 
12346.00000      326          1  77183.60000
12347.00000        3          7   4310.00000
12348.00000       76          4   1797.24000
12349.00000       19          1   1757.55000
12350.00000      311          1    334.40000
12352.00000       37          8   2506.04000
12353.00000      205          1     89.00000
12354.00000      233          1   1079.40000
12355.00000      215          1    459.40000
12356.00000       23          3   2811.43000
12357.00000       34          1   6207.67000
12358.00000        2          2   1168.06000
12359.00000       58          4   6372.58000
12360.00000       53          3   2662.06000
12361.00000      288          1    189.90000
12362.00000        4         10   5226.23000
12363.00000      110          2    552.00000
12364.00000        8          4   1313.10000
12365.00000      292          2    641.38000
12367.00000        5          1    168.90000
12370.00000       52          4   3545.69000
12371.00000       45          2   1887.96000
12372.00000       72          3   1298.04000
12373.00000      312          1    364.60000
12374.00000       26          1    742.93000
12375.00000       11          2    457.50000
12377.00000      316          2   1628.12000
12378.00000      130          1   4008.62000
12379.00000       82          2    852.24000
12380.00000       22          4   2724.81000
12381.00000        5          5   1845.31000
12383.00000      185          5   1850.56000
12384.00000       29          2    585.27000
12386.00000      338          2    401.90000
12388.00000       16          6   2780.66000
12390.00000       80          1    549.84000
12391.00000       22          1    460.89000
12393.00000       73          4   1582.60000
12394.00000       64          2   1272.48000
12395.00000       20         12   3018.63000
12397.00000       36          2   2409.90000
12398.00000       46          1   1635.66000
12399.00000      120          4   1108.65000
12401.00000      304          1     84.30000
12402.00000      324          1    225.60000
12403.00000       50          1    427.70000
12405.00000      149          1   1710.39000
12406.00000       23          2   3415.30000
12407.00000       50          5   1708.12000
12408.00000       33          5   2888.55000
12409.00000       79          3  11072.67000
12410.00000      309          2    693.33000
12412.00000       75          3   1226.88000
12413.00000       67          3    758.10000
12414.00000      218          3    562.41000
12415.00000       25         21 124914.53000
12417.00000        4          9   3649.10000
12418.00000      113          1    668.58000
12420.00000       64          1    600.39000
12421.00000       16          4    807.04000
12422.00000       96          3    803.56000
12423.00000        1          8   1859.31000
12424.00000      163          2   1760.96000
12425.00000       79          1    777.20000
12426.00000      195          1    582.73000
12427.00000       22          3    825.80000
12428.00000       26          9   7956.46000
12429.00000       10          4   3750.40000
12430.00000       44          1    256.40000
12431.00000       36         15   6487.45000
12432.00000       43          5   5059.32000
12433.00000        1          7  13375.87000
12434.00000       85          2    806.14000
12435.00000       80          2   7829.89000
12436.00000      100          1    509.01000
12437.00000        2         18   4951.41000
12438.00000       15          2   2906.85000
12441.00000      367          1    173.55000
12442.00000        4          1    172.06000
12444.00000       22          5   5005.46000
12445.00000       23          1    133.40000
12446.00000       58          1   1002.31000
12447.00000      244          1    476.49000
12448.00000       45          1    449.45000
12449.00000       23          4   4067.29000
12450.00000      157          2    197.88000
12451.00000       11          5   9035.52000
12452.00

In [16]:
rfm.describe().T

count       mean        std     min       25%       50%  \
recency   4338.00000   93.05947  100.01226 1.00000  18.00000  51.00000   
frequency 4338.00000    4.27271    7.70622 1.00000   1.00000   2.00000   
monetary  4338.00000 2054.27061 8989.22990 3.75000 307.41500 674.48500   

                 75%          max  
recency    142.75000    374.00000  
frequency    5.00000    210.00000  
monetary  1661.74000 280206.02000

### Görev 3: RFM skorlarının oluşturulması ve tek bir değişkene çevrilmesi
* Recency, Frequency ve Monetary metriklerini qcut yardımı ile 1-5 arasında skorlara çeviriniz.
* Bu skorları recency_score, frequency_score ve monetary_score olarak kaydediniz.
* Oluşan 3 farklı değişkenin değerini tek bir değişken olarak ifade ediniz ve RFM_SCORE olarak kaydediniz.
* Örneğin; Ayrı ayrı değişkenlerde sırasıyla 5, 2, 1 olan recency_score, frequency_score ve monetary_score skorlarını RFM_SCORE değişkeni isimlendirmesi ile 521 olarak oluşturunuz.

In [17]:
rfm["recency_score"] = pd.qcut(rfm['recency'], 5, labels=[5, 4, 3, 2, 1])
rfm["frequency_score"] = pd.qcut(rfm['frequency'].rank(method="first"), 5, labels=[1, 2, 3, 4, 5])
rfm["monetary_score"] = pd.qcut(rfm['monetary'], 5, labels=[1, 2, 3, 4, 5])
rfm

recency  frequency     monetary recency_score frequency_score  \
Customer ID                                                                  
12346.00000      326          1  77183.60000             1               1   
12347.00000        3          7   4310.00000             5               5   
12348.00000       76          4   1797.24000             2               4   
12349.00000       19          1   1757.55000             4               1   
12350.00000      311          1    334.40000             1               1   
12352.00000       37          8   2506.04000             3               5   
12353.00000      205          1     89.00000             1               1   
12354.00000      233          1   1079.40000             1               1   
12355.00000      215          1    459.40000             1               1   
12356.00000       23          3   2811.43000             4               3   
12357.00000       34          1   6207.67000             3               1   
12358.00000        2          2   1168.06000             5               2   
12359.00000       58          4   6372.58000             3               4   
12360.00000       53          3   2662.06000             3               3   
12361.00000      288          1    189.90000             1               1   
12362.00000        4         10   5226.23000             5               5   
12363.00000      110          2    552.00000             2               2   
12364.00000        8          4   1313.10000             5               4   
12365.00000      292          2    641.38000             1               2   
12367.00000        5          1    168.90000             5               1   
12370.00000       52          4   3545.69000             3               4   
12371.00000       45          2   1887.96000             3               2   
12372.00000       72          3   1298.04000             3               3   
12373.00000      312          1    364.60000             1               1   
12374.00000       26          1    742.93000             4               1   
12375.00000       11          2    457.50000             5               2   
12377.00000      316          2   1628.12000             1               2   
12378.00000      130          1   4008.62000             2               1   
12379.00000       82          2    852.24000             2               2   
12380.00000       22          4   2724.81000             4               4   
12381.00000        5          5   1845.31000             5               4   
12383.00000      185          5   1850.56000             1               4   
12384.00000       29          2    585.27000             4               2   
12386.00000      338          2    401.90000             1               2   
12388.00000       16          6   2780.66000             4               4   
12390.00000       80          1    549.84000             2               1   
12391.00000       22          1    460.89000             4               1   
12393.00000       73          4   1582.60000             2               4   
12394.00000       64          2   1272.48000             3               2   
12395.00000       20         12   3018.63000             4               5   
12397.00000       36          2   2409.90000             3               2   
12398.00000       46          1   1635.66000             3               1   
12399.00000      120          4   1108.65000             2               4   
12401.00000      304          1     84.30000             1               1   
12402.00000      324          1    225.60000             1               1   
12403.00000       50          1    427.70000             3               1   
12405.00000      149          1   1710.39000             2               1   
12406.00000       23          2   3415.30000             4               2   
12407.00000       50          5   1708.12000             3               4   
12408.00000       33          5   2

In [18]:
rfm["RFM_SCORE"] = (rfm['recency_score'].astype(str) +
                    rfm['frequency_score'].astype(str))
rfm

recency  frequency     monetary recency_score frequency_score  \
Customer ID                                                                  
12346.00000      326          1  77183.60000             1               1   
12347.00000        3          7   4310.00000             5               5   
12348.00000       76          4   1797.24000             2               4   
12349.00000       19          1   1757.55000             4               1   
12350.00000      311          1    334.40000             1               1   
12352.00000       37          8   2506.04000             3               5   
12353.00000      205          1     89.00000             1               1   
12354.00000      233          1   1079.40000             1               1   
12355.00000      215          1    459.40000             1               1   
12356.00000       23          3   2811.43000             4               3   
12357.00000       34          1   6207.67000             3               1   
12358.00000        2          2   1168.06000             5               2   
12359.00000       58          4   6372.58000             3               4   
12360.00000       53          3   2662.06000             3               3   
12361.00000      288          1    189.90000             1               1   
12362.00000        4         10   5226.23000             5               5   
12363.00000      110          2    552.00000             2               2   
12364.00000        8          4   1313.10000             5               4   
12365.00000      292          2    641.38000             1               2   
12367.00000        5          1    168.90000             5               1   
12370.00000       52          4   3545.69000             3               4   
12371.00000       45          2   1887.96000             3               2   
12372.00000       72          3   1298.04000             3               3   
12373.00000      312          1    364.60000             1               1   
12374.00000       26          1    742.93000             4               1   
12375.00000       11          2    457.50000             5               2   
12377.00000      316          2   1628.12000             1               2   
12378.00000      130          1   4008.62000             2               1   
12379.00000       82          2    852.24000             2               2   
12380.00000       22          4   2724.81000             4               4   
12381.00000        5          5   1845.31000             5               4   
12383.00000      185          5   1850.56000             1               4   
12384.00000       29          2    585.27000             4               2   
12386.00000      338          2    401.90000             1               2   
12388.00000       16          6   2780.66000             4               4   
12390.00000       80          1    549.84000             2               1   
12391.00000       22          1    460.89000             4               1   
12393.00000       73          4   1582.60000             2               4   
12394.00000       64          2   1272.48000             3               2   
12395.00000       20         12   3018.63000             4               5   
12397.00000       36          2   2409.90000             3               2   
12398.00000       46          1   1635.66000             3               1   
12399.00000      120          4   1108.65000             2               4   
12401.00000      304          1     84.30000             1               1   
12402.00000      324          1    225.60000             1               1   
12403.00000       50          1    427.70000             3               1   
12405.00000      149          1   1710.39000             2               1   
12406.00000       23          2   3415.30000             4               2   
12407.00000       50          5   1708.12000             3               4   
12408.00000       33          5   2

In [19]:
rfm.describe().T

count       mean        std     min       25%       50%  \
recency   4338.00000   93.05947  100.01226 1.00000  18.00000  51.00000   
frequency 4338.00000    4.27271    7.70622 1.00000   1.00000   2.00000   
monetary  4338.00000 2054.27061 8989.22990 3.75000 307.41500 674.48500   

                 75%          max  
recency    142.75000    374.00000  
frequency    5.00000    210.00000  
monetary  1661.74000 280206.02000

In [20]:
rfm[rfm["RFM_SCORE"] == "55"].head()  # champions

recency  frequency    monetary recency_score frequency_score  \
Customer ID                                                                 
12347.00000        3          7  4310.00000             5               5   
12362.00000        4         10  5226.23000             5               5   
12417.00000        4          9  3649.10000             5               5   
12423.00000        1          8  1859.31000             5               5   
12433.00000        1          7 13375.87000             5               5   

            monetary_score RFM_SCORE  
Customer ID                           
12347.00000              5        55  
12362.00000              5        55  
12417.00000              5        55  
12423.00000              4        55  
12433.00000              5        55

In [21]:
rfm[rfm["RFM_SCORE"] == "11"].head()  # hibernating

recency  frequency    monetary recency_score frequency_score  \
Customer ID                                                                 
12346.00000      326          1 77183.60000             1               1   
12350.00000      311          1   334.40000             1               1   
12353.00000      205          1    89.00000             1               1   
12354.00000      233          1  1079.40000             1               1   
12355.00000      215          1   459.40000             1               1   

            monetary_score RFM_SCORE  
Customer ID                           
12346.00000              5        11  
12350.00000              2        11  
12353.00000              1        11  
12354.00000              4        11  
12355.00000              2        11

### Görev 4:
* RFM skorlarının segment olarak tanımlanması
* Oluşturulan RFM skorların daha açıklanabilir olması için segment tanımlamaları yapınız.
* Aşağıdaki seg_map yardımı ile skorları segmentlere çeviriniz.

In [23]:
seg_map = {
    r'[1-2][1-2]': 'hibernating',
    r'[1-2][3-4]': 'at_Risk',
    r'[1-2]5': 'cant_loose',
    r'3[1-2]': 'about_to_sleep',
    r'33': 'need_attention',
    r'[3-4][4-5]': 'loyal_customers',
    r'41': 'promising',
    r'51': 'new_customers',
    r'[4-5][2-3]': 'potential_loyalists',
    r'5[4-5]': 'champions'
}

In [24]:
rfm['segment'] = rfm['RFM_SCORE'].replace(seg_map, regex=True)
rfm.head()

recency  frequency    monetary recency_score frequency_score  \
Customer ID                                                                 
12346.00000      326          1 77183.60000             1               1   
12347.00000        3          7  4310.00000             5               5   
12348.00000       76          4  1797.24000             2               4   
12349.00000       19          1  1757.55000             4               1   
12350.00000      311          1   334.40000             1               1   

            monetary_score RFM_SCORE      segment  
Customer ID                                        
12346.00000              5        11  hibernating  
12347.00000              5        55    champions  
12348.00000              4        24      at_Risk  
12349.00000              4        41    promising  
12350.00000              2        11  hibernating

### Görev 5:
Önemli bulduğunuz 3 segmenti seçiniz. Bu üç segmenti;
* Hem aksiyon kararları açısından,
* Hem de segmentlerin yapısı açısından (ortalama RFM değerleri) yorumlayınız.
  
"Loyal Customers" sınıfına ait customer ID'leri seçerek excel çıktısını alınız.

In [25]:
rfm["Country"] = df["Country"]

In [26]:
rfm[["segment", "recency", "frequency", "monetary"]].groupby(["segment"]).agg(["mean","count"])

recency       frequency         monetary      
                         mean count      mean count       mean count
segment                                                             
about_to_sleep       53.31250   352   1.16193   352  471.99437   352
at_Risk             153.78583   593   2.87858   593 1084.53530   593
cant_loose          132.96825    63   8.38095    63 2796.15587    63
champions             6.36177   633  12.41706   633 6857.96392   633
hibernating         217.60504  1071   1.10177  1071  488.64331  1071
loyal_customers      33.60806   819   6.47985   819 2864.24779   819
need_attention       52.42781   187   2.32620   187  897.62786   187
new_customers         7.42857    42   1.00000    42  388.21286    42
potential_loyalists  17.39876   484   2.01033   484 1041.22200   484
promising            23.51064    94   1.00000    94  294.00798    94

In [27]:
rfm.groupby(['segment',"Country"]).agg({"segment":"count"})

segment
segment             Country                
about_to_sleep      EIRE                  2
                    France                2
                    Iceland               1
                    United Kingdom      167
at_Risk             France               13
                    Germany               5
                    Iceland               3
                    United Kingdom      302
cant_loose          Germany               1
                    United Kingdom       36
champions           Australia             1
                    EIRE                  3
                    France                9
                    Germany               2
                    Iceland               2
                    Portugal              1
                    United Kingdom      379
hibernating         Australia             1
                    EIRE                  7
                    France               12
                    Germany               4
                    Iceland               4
                    Portugal              1
                    United Kingdom      554
loyal_customers     Australia             3
                    EIRE                  2
                    France                6
                    Germany               5
                    Iceland               4
                    Portugal              1
                    United Kingdom      433
need_attention      France                3
                    United Kingdom      105
new_customers       EIRE                  1
                    Iceland               1
                    United Kingdom       21
potential_loyalists EIRE                  2
                    France                8
                    Germany               2
                    Iceland               1
                    Portugal              1
                    United Kingdom      260
promising           EIRE                  1
                    Iceland               5
                    United Kingdom       49

In [28]:
rfm[rfm["segment"] == "at_Risk"].head()

recency  frequency    monetary recency_score frequency_score  \
Customer ID                                                                 
12348.00000       76          4  1797.24000             2               4   
12383.00000      185          5  1850.56000             1               4   
12393.00000       73          4  1582.60000             2               4   
12399.00000      120          4  1108.65000             2               4   
12409.00000       79          3 11072.67000             2               3   

            monetary_score RFM_SCORE  segment         Country  
Customer ID                                                    
12348.00000              4        24  at_Risk  United Kingdom  
12383.00000              4        14  at_Risk  United Kingdom  
12393.00000              4        24  at_Risk  United Kingdom  
12399.00000              4        24  at_Risk  United Kingdom  
12409.00000              5        23  at_Risk  United Kingdom

In [29]:
rfm[rfm["segment"] == "new_customers"].head()

recency  frequency  monetary recency_score frequency_score  \
Customer ID                                                               
12367.00000        5          1 168.90000             5               1   
12442.00000        4          1 172.06000             5               1   
12478.00000        4          1 680.99000             5               1   
12479.00000       12          1 527.20000             5               1   
12558.00000        8          1 269.96000             5               1   

            monetary_score RFM_SCORE        segment         Country  
Customer ID                                                          
12367.00000              1        51  new_customers  United Kingdom  
12442.00000              1        51  new_customers            EIRE  
12478.00000              3        51  new_customers  United Kingdom  
12479.00000              3        51  new_customers  United Kingdom  
12558.00000              2        51  new_customers  United Kingdom

In [30]:
rfm[rfm["segment"] == "potential_loyalists"].head()

recency  frequency   monetary recency_score frequency_score  \
Customer ID                                                                
12356.00000       23          3 2811.43000             4               3   
12358.00000        2          2 1168.06000             5               2   
12375.00000       11          2  457.50000             5               2   
12384.00000       29          2  585.27000             4               2   
12406.00000       23          2 3415.30000             4               2   

            monetary_score RFM_SCORE              segment         Country  
Customer ID                                                                
12356.00000              5        43  potential_loyalists  United Kingdom  
12358.00000              4        52  potential_loyalists  United Kingdom  
12375.00000              2        52  potential_loyalists  United Kingdom  
12384.00000              3        42  potential_loyalists  United Kingdom  
12406.00000              5        42  potential_loyalists  United Kingdom

In [31]:
new_df = pd.DataFrame()
new_df["loyal_customers"] = rfm[rfm["segment"] == "loyal_customers"].index
new_df.head()

loyal_customers
0      12352.00000
1      12359.00000
2      12370.00000
3      12380.00000
4      12388.00000

In [32]:
new_df.to_excel("loyal_customers.xlsx")

### Aksiyon Planları:
* İlk seçtiğim segment At Risk olanlar. Bu grubu tekrar işlem yaptırabilirsek Loyal Customer segmentine geçiş yapacaklardır. Bu segmentin parası var, işlem sıklığı da recency değerine bağlı olarak artacaktır. Örneğin 6 ay ve üzeri süredir müşterimiz olan ve 1000 birim para harcamış kişilere  konsol, bilgisayar, müzik sistemleri ve TV gibi fiyatı görece yüksek ve eğlenceye hizmet eden çeşitli teknolojik ürünlerde yapacağımız kampanyalarla bu kesimi yakalama şansımız bir hayli yüksektir.

* İkinci seçtiğim segment Potential Loyalists. Bu grubu da Loyal Customer segmentine yükseltebilmemiz için işlem sıklığı çok önemli. Bu grubun da günlük ev ihtiyaçları ve market alışverişi gibi ürünleri buradan satın almasını sağlamak için bu ürünlerde belli bir sayı bazında indirim yapılabilir. Örneğin; 3 paket makarna %15 indirimli ve kargo bedava gibi. Bu şekilde birim fiyatı düşük ama birden fazla adet satın alım yaptırarak artık günlük ihitiyaçları buradan satın aldırma alışkanlığını da kazandırırsak bu grubun işlem sıklığı artarak devam eder.

* Üçüncü seçtiğim segment New Customers. Bu müşteriler yeni müşteriler, bir şekilde burayı tercih etmeye başlamışlar. Bu grubun burada iyi hizmet almaya devam etmesi gerekir. Yeni müşteri memnun kaldığı yeri Word-of-Mouth Marketing prensibiyle yeni müşteri kazandıracak kişiler olarak görmek gerekir. Aldığı tatmin edici hizmet yeni müşterileri de buraya çekecektir ve kendisi de sadık müşteri olma yolunda ilerleyecektir. Bu müşteri türünü yakalamanın ve elde tutmanın yollarından birisi çeşitli hobi, kıyafet ya da ev tekstili gibi ürünleri avantajlı bir fiyata burada bulmasını sağlamaktır. Bu müşterilerin Monetary ortalaması 388, yani görece ucuz ürünü almışlar ve müşteri olmuşlar. Örneğin; kutu oyunları, halı, ya da kışlık ceket gibi bu segmentin giriş-orta düzey ürünleriyle bunlara bir alışkanlık kazandırmak bu müşterileri elde tutar.
